In [1]:
import json
import os

def load_jsonl(file):
    with open(file, 'r') as f:
        return [json.loads(line) for line in f]


In [10]:
base_dir = "output_32K"

input_file = os.path.join(base_dir, "filtered_dataset.json")
output_file = os.path.join(base_dir, "final_dataset.json")

with open(input_file, "r") as f:
    data = json.load(f)

yes_entries = []
no_entries = []
yes_count = 0
no_count = 0

for entry in data:
    # Get the response text
    response = entry.get("is_hard", "")
    # Split by lines and take the last non-empty line
    lines = [line.strip() for line in response.strip().splitlines() if line.strip()]
    if not lines:
        continue  # skip if no content is available
    final_line = lines[-1]

    prompt = f"""{entry['prompt_goal']}
Repository: {entry["repo_text"]}
Question: {entry["question"]}
"""

    entry['prompt'] = prompt

    if final_line == "Yes":
        yes_count += 1
        yes_entries.append(entry)
    elif final_line == "No":
        no_count += 1
        no_entries.append(entry)

with open(output_file, "w") as f:
    json.dump(yes_entries, f, indent=4)

print(yes_count, no_count)

327 267


In [13]:
data = "output_1M/final_dataset.json"
with open(data, "r") as f:
    data = json.load(f)


In [58]:
print(data[0].keys())

dict_keys(['prompt', 'generation', 'correct_letter', 'question', 'repo_text', 'prompt_goal', 'repo'])


In [12]:


# Convert the list to a dictionary with keys 0, 1, 2, etc.
data_dict = dict(enumerate(data))

# Optionally, write the new dictionary to a file
with open("output_1M/dataset_1M.json", "w") as outfile:
    json.dump(data_dict, outfile, indent=4)


In [13]:
# Load the JSON file created above
with open("output_1M/dataset_1M.json", "r") as f:
    data_dict = json.load(f)

In [15]:
data_dict[0]

KeyError: 0

In [18]:
print(data[0]["prompt"])

You are going to be provided the content of a
repository and a question about it. Provide the answer to the question by
stating ONLY the letter associated to the question.
Repository:
[start of .git-blame-ignore-revs]
# Linting/formatting:
# isort/pyupgrade -> Ruff:
4f3e794a69e84e4294c605c669e4d1876a18dd50
# Black -> Ruff format:
419398d1dd9f3c0babdcfde1d52c249266f59ef0
# Ruff 0.2.1:
918402f01d82694214ff93cd77ff62d5d5beb1ab
# Ruff 0.4.8:
332e77ba3b658c2a57fc72f832587b72311d87c7

[end of .git-blame-ignore-revs]
[start of mkdocs.yml]
site_name: Pydantic
site_description: Data validation using Python type hints
strict: true
site_url: https://docs.pydantic.dev/

theme:
  name: 'material'
  custom_dir: 'docs/theme'
  palette:
  - media: "(prefers-color-scheme)"
    scheme: default
    primary: pink
    accent: pink
    toggle:
      icon: material/lightbulb
      name: "Switch to light mode"
  - media: "(prefers-color-scheme: light)"
    scheme: default
    primary: pink
    accent: pink
  

In [14]:
base_dir = "output_1M"

file_path = os.path.join(base_dir, "final_dataset.json")

prompts = json.load(open(file_path, "r"))

In [15]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("meta-llama/Llama-3.1-405B")

def count_tokens(text):
    return len(tokenizer.encode(text))

kept_prompts = []
for i, prompt in enumerate(prompts):
    prompt = prompt["repo_text"]
    num_tokens = count_tokens(prompt)
    if num_tokens <= 1000000:
        kept_prompts.append(prompt)
        print(f"Prompt {i} is {num_tokens} tokens")
    else:
        print(f"Prompt {i} is too long: {num_tokens} tokens")


Token indices sequence length is longer than the specified maximum sequence length for this model (877403 > 131072). Running this sequence through the model will result in indexing errors


Prompt 0 is 877403 tokens
Prompt 1 is 877403 tokens
Prompt 2 is 877403 tokens
Prompt 3 is 877403 tokens
Prompt 4 is 877403 tokens
Prompt 5 is 877403 tokens
Prompt 6 is 877403 tokens
Prompt 7 is 877403 tokens
Prompt 8 is 877403 tokens
Prompt 9 is 877403 tokens
Prompt 10 is 877403 tokens
Prompt 11 is 877403 tokens
Prompt 12 is 877403 tokens
Prompt 13 is 877403 tokens
Prompt 14 is 877403 tokens
Prompt 15 is 877403 tokens
Prompt 16 is 877403 tokens
Prompt 17 is 877403 tokens
Prompt 18 is 877403 tokens
Prompt 19 is 877403 tokens
Prompt 20 is 742921 tokens
Prompt 21 is 742921 tokens
Prompt 22 is 742921 tokens
Prompt 23 is 742921 tokens
Prompt 24 is 742921 tokens
Prompt 25 is 742921 tokens
Prompt 26 is 742921 tokens
Prompt 27 is 742921 tokens
Prompt 28 is 742921 tokens
Prompt 29 is 742921 tokens
Prompt 30 is 742921 tokens
Prompt 31 is 742921 tokens
Prompt 32 is 742921 tokens
Prompt 33 is 742921 tokens
Prompt 34 is 742921 tokens
Prompt 35 is 742921 tokens
Prompt 36 is 742921 tokens
Prompt 37 i

In [ ]:


# kept_data = []

# tokenizer = AutoTokenizer.from_pretrained("Qwen/Qwen2.5-14B-Instruct-1M")

# print(f"Loaded {len(data)} entries")

# for i, entry in enumerate(data):
#     prompt = entry["prompt"]
#     num_tokens = len(tokenizer.encode(prompt))
#     if num_tokens <= 256000:
#         kept_data.append(entry)

# print(f"Kept {len(kept_data)} entries")


In [111]:
data_dir = "dataset/output_512K/results/Qwen2.5-14B-Instruct-1M-eval.jsonl"

data = load_jsonl(data_dir)

num_correct = 0

for entry in data:
    if "yes" in entry["is_correct"].lower():
        num_correct += 1
        
print(f"Number of correct entries: {num_correct}")
print(f"Number of incorrect entries: {len(data) - num_correct}")
print(f"Number of entries: {len(data)}")
print(f"Accuracy: {num_correct / len(data)}")

Number of correct entries: 105
Number of incorrect entries: 23
Number of entries: 128
Accuracy: 0.8203125


In [18]:
data_dir = "dataset/output_64K/results/gemini-eval.jsonl"

data = load_jsonl(data_dir)

num_correct = 0

for entry in data:
    if "yes" in entry.get("is_correct", "").lower():
        num_correct += 1
        
print(f"Number of correct entries: {num_correct}")
print(f"Number of incorrect entries: {len(data) - num_correct}")
print(f"Number of entries: {len(data)}")
print(f"Accuracy: {num_correct / len(data)}")

Number of correct entries: 129
Number of incorrect entries: 41
Number of entries: 170
Accuracy: 0.7588235294117647


In [14]:
input_file = "dataset/gemini-results/gemini_1M.json"

with open(input_file, "r") as f:
    gpt_answer = json.load(f)["results"]

In [15]:
empty_count = 0

for entry in gpt_answer:
    if entry['text'] == "":
        empty_count += 1

print(f"Number of empty entries: {empty_count}")

Number of empty entries: 43


In [11]:
83/102

0.8137254901960784

In [ ]:
empty_gen = 0

for entry in data:
    if entry[]

''

In [4]:
data_dir = "dataset/output_64K/results/gpt4o-eval.jsonl"

data = load_jsonl(data_dir)

num_correct = 0

for entry in data:
    if "yes" in entry["is_correct"].lower():
        num_correct += 1
        
print(f"Number of correct entries: {num_correct}")
print(f"Number of incorrect entries: {len(data) - num_correct}")
print(f"Number of entries: {len(data)}")
print(f"Accuracy: {num_correct / len(data)}")

Number of correct entries: 142
Number of incorrect entries: 28
Number of entries: 170
Accuracy: 0.8352941176470589


In [110]:
data_dir = "dataset/output_1M/results/AI21-Jamba-1.5-Large-eval.jsonl"

data = load_jsonl(data_dir)

num_correct = 0

for entry in data:
    if "yes" in entry["is_correct"].lower():
        num_correct += 1
        
print(f"Number of correct entries: {num_correct}")
print(f"Number of incorrect entries: {len(data) - num_correct}")
print(f"Number of entries: {len(data)}")
print(f"Accuracy: {num_correct / len(data)}")

Number of correct entries: 18
Number of incorrect entries: 18
Number of entries: 36
Accuracy: 0.5


In [5]:
data_dir = "dataset/output_128K/results/Llama-3.1_405B-Instruct-eval.jsonl"

data = load_jsonl(data_dir)

num_correct = 0

for entry in data:
    if "yes" in entry["is_correct"].lower():
        num_correct += 1
        
print(f"Number of correct entries: {num_correct}")
print(f"Number of incorrect entries: {len(data) - num_correct}")
print(f"Number of entries: {len(data)}")
print(f"Accuracy: {num_correct / len(data)}")

Number of correct entries: 239
Number of incorrect entries: 47
Number of entries: 286
Accuracy: 0.8356643356643356


In [6]:
239/281

0.8505338078291815

In [42]:
import pandas as pd
import json
import glob

def normalize_is_correct(value):
    """
    Convert various representations of correctness into a boolean.
    Returns True if the value indicates a correct answer, otherwise False.
    If no answer is provided, returns None.
    """
    if isinstance(value, str):
        return True if "yes" in value.lower() else False
    return None

def load_results(file_path):
    """Load a JSONL file into a DataFrame."""
    records = []
    with open(file_path, 'r') as f:
        for line in f:
            line = line.strip()
            if line:
                records.append(json.loads(line))
    return pd.DataFrame(records)

# Adjust this pattern to match the location of your results files.
results_files = glob.glob("dataset/output_64K/results/*-eval.jsonl")

# Dictionary to hold DataFrames for each model.
dfs = {}

for file in results_files:
    # Derive a model name from the file name.
    model_name = file.split("/")[-1].replace(".jsonl", "")
    df = load_results(file)
    
    # Ensure there is a key to join on. If "question" is missing, use "prompt".
    if "question" not in df.columns:
        df["question"] = df["prompt"]
    
    # Normalize the is_correct field if present.
    if "is_correct" in df.columns:
        df[f"{model_name}_is_correct"] = df["is_correct"].apply(
            lambda x: normalize_is_correct(x) if pd.notnull(x) else None
        )
    else:
        df[f"{model_name}_is_correct"] = None
        
    # Keep only the "question" and model-specific is_correct columns.
    dfs[model_name] = df[["question", f"{model_name}_is_correct"]]

# Merge all DataFrames on the 'question' key using an outer join.
merged_df = None
for model_name, df in dfs.items():
    if merged_df is None:
        merged_df = df
    else:
        merged_df = pd.merge(merged_df, df, on="question", how="outer")

# Optionally, fill missing values with a string such as "didn't answer"
# merged_df.fillna("didn't answer", inplace=True)

import numpy as np

def compute_correct_percentage(row):
    # Select columns that end with '_is_correct'
    is_correct_cols = [col for col in row.index if col.endswith('_is_correct')]
    # Filter out models that did not answer (i.e. NaN values)
    answered = [row[col] for col in is_correct_cols if pd.notnull(row[col])]
    if not answered:
        return np.nan  # No model answered the question
    # Calculate the percentage of True values among the answered
    percentage = (sum(answered) / len(answered)) * 100
    return percentage

# Apply the function row-wise to create a new column.
merged_df['percent_correct'] = merged_df.apply(compute_correct_percentage, axis=1)

# Display the updated DataFrame.
merged_df.head()



question  \
0  Question:\nAfter an update in the h11 library,...   
1  Question:\nAs of version 1.0.6, which version ...   
2  Question:\nCan ASGI HTTP extensions, such as `...   
3  Question:\nHow does `StreamingIterator` from r...   
4  Question:\nHow does pathspec handle exclusions...   

   Llama-3.1_405B-Instruct-eval_is_correct  \
0                                     True   
1                                    False   
2                                     True   
3                                     True   
4                                     True   

   AI21-Jamba-1.5-Large-eval_is_correct  \
0                                  True   
1                                 False   
2                                  True   
3                                  True   
4                                  True   

   Qwen2.5-14B-Instruct-1M-eval_is_correct  percent_correct  
0                                     True       100.000000  
1                                    False         0.000000  
2                                     True       100.000000  
3                                    False        66.666667  
4                                     True       100.000000

In [43]:
merged_df["percent_correct"].value_counts()

percent_correct
100.000000    109
66.666667      27
33.333333      20
0.000000       14
Name: count, dtype: int64

In [45]:
# Print the questions that all models got wrong

wrong_questions = merged_df[merged_df["percent_correct"] == 0]
wrong_questions = wrong_questions[["question"]]
wrong_questions = wrong_questions.drop_duplicates()

for index, row in wrong_questions.iterrows():
    print(row["question"])
    print("\n")
    

Question:
As of version 1.0.6, which version of Python is no longer supported by the codebase?
A) Python 3.8
B) Python 3.7
C) Python 3.6
D) Python 2.7



Question:
In the PyJWT library, what happens if you pass an `algorithm` parameter to the `encode` method and also specify a different algorithm in the 'alg' field of the headers?
A) The `encode` method raises an error due to conflicting algorithm specifications.
B) The algorithm specified in the headers is used, ignoring the one in the `encode` method.
C) Both algorithms are encoded in the token, causing an invalid token.
D) The algorithm specified in the `encode` method overwrites the one in the headers.



Question:
In the `pyjwt` library, how should the `PyJWTError` be imported to avoid an `AttributeError`?
A) import pyjwt.exceptions.PyJWTError
B) import jwt.exceptions.Error.PyJWTError
C) import jwt.exceptions.PyJWTError
D) import jwt.PyJWTError



Question:
In the `requests-toolbelt` library, how should you encode dictionary value

In [65]:
data_dir = "dataset/output_1M/results/AI21-Jamba-1.5-Large.jsonl"

data = load_jsonl(data_dir)



In [80]:
import random

idx = random.randint(0, len(data) - 1)

print(data[idx]["generation"], data[idx]["correct_letter"])

 C. C


In [ ]:
data = "dataset/output_1M/results/Qwen2.5-14B-Instruct-1M.jsonl"

data = load_jsonl(data)


To answer the question about the behavior of `sys.exit(0)` within a span in version 1.31.0 of the OpenTelemetry SDK, we need to analyze the relevant parts of the provided code and documentation.

### Analysis:

1. **Understanding `sys.exit(0)` Behavior:**
   - `sys.exit(0)` is a standard Python function that raises a `SystemExit` exception, which is a subclass of `BaseException`. When this exception is raised, it typically terminates the program.

2. **OpenTelemetry Span Context and Exception Handling:**
   - OpenTelemetry SDKs are designed to handle exceptions within spans. When an exception is raised within a span, the SDK can record the exception details, including the type and message, as part of the span's attributes.

3. **Relevant Code in `opentelemetry-sdk/src/opentelemetry/sdk/trace/id_generator.py`:**
   - The code snippet provided in the repository shows that the `sys.exit(0)` call is handled within a span. Specifically, the `sys.exit(0)` call raises a `SystemExit` exception

In [104]:
idx = random.randint(0, len(data) - 1)

print(data[idx]["generation"], data[idx]["correct_letter"])

Final Answer: B

Explanation:
The correct answer is B. The issue described in the repository text is related to the dynamic calculation of dependencies in CFFI's `setup.py`. Specifically, the text mentions that `pycparser` is not actually required for PyPy, but `setup.py` incorrectly lists it as a required dependency dynamically during the sdist build under CPython. This discrepancy causes `pip check` to report `pycparser` as missing in a PyPy build, even though it is not actually required for PyPy. The other options are incorrect because:

- A) is incorrect because `pycparser` is not a mandatory dependency for all builds of CFFI, especially not for PyPy.
- C) is incorrect because the issue is not with `pip` itself but with the way CFFI's `setup.py` dynamically calculates dependencies.
- D) is incorrect because PyPy does support `pycparser`, and the issue is not about PyPy's support for `pycparser` but about the incorrect dependency listing in `setup.py`. B
